In [1]:
import os
os.chdir(r"C:\Users\cdron\Desktop\Cleanup\Misc\kaggle\Facebook_rec_4\source")
os.getcwd()

'C:\\Users\\cdron\\Desktop\\Cleanup\\Misc\\kaggle\\Facebook_rec_4\\source'

In [12]:
import csv
from csv import DictReader
import numpy as np

In [13]:
features = ['bidder_id', 'bid_num', 'avg_auction_times', 'avg_auction', 'auc_device', 'auc_country', 'auc_ip', 'auc_url',
            'auc_device_max', 'auc_country_max', 'auc_ip_max', 'auc_url_max',
            'auc_device_min', 'auc_country_min', 'auc_ip_min', 'auc_url_min',
            'auc_num', 'max_merch', 'merch_num', 'max_device', 'device_num', 'max_country',
            'country_num', 'max_ip', 'ip_num', 'max_url', 'url_num', 'avg_times', 'min_times', 'max_times',
            'min_amount', 'avg_amount', 'max_amount', 'success_num'] 

In [14]:
filename = 'bids.csv'

In [23]:
open_file = open("arrange1.csv",'wb')
open_file_object = csv.writer(open_file)
open_file_object.writerow(features)
writable = dict()
last_row = dict()
write_row = list()
write_rows = list()
count = 0

In [33]:
def update_writable(writable, row):
    writable.setdefault('num', 0)
    writable.setdefault('auction', dict())
    writable.setdefault('merchandise', dict())
    writable.setdefault('device', dict())
    writable.setdefault('country', dict())
    writable.setdefault('ip', dict())
    writable.setdefault('url', dict())
    writable.setdefault('time', dict())
    writable['num'] += 1
    # Update each auction the bidder has particapated
    writable['auction'].setdefault(row['auction'], dict())
    writable['auction'][row['auction']].setdefault('device', dict())
    writable['auction'][row['auction']].setdefault('country', dict())
    writable['auction'][row['auction']].setdefault('ip', dict())
    writable['auction'][row['auction']].setdefault('url', dict())
    writable['auction'][row['auction']].setdefault('time', dict())
    writable['auction'][row['auction']].setdefault('amount', 0)
    writable['auction'][row['auction']].setdefault('success', 0)
    writable['auction'][row['auction']]['device'].setdefault(row['device'], 0)
    writable['auction'][row['auction']]['country'].setdefault(row['country'], 0)
    writable['auction'][row['auction']]['ip'].setdefault(row['ip'], 0)
    writable['auction'][row['auction']]['url'].setdefault(row['url'], 0)
    writable['auction'][row['auction']]['time'].setdefault(row['time'], 0)
    writable['auction'][row['auction']]['device'][row['device']] += 1
    writable['auction'][row['auction']]['country'][row['country']] += 1
    writable['auction'][row['auction']]['ip'][row['ip']] += 1
    writable['auction'][row['auction']]['url'][row['url']] += 1
    writable['auction'][row['auction']]['time'][row['time']] += 1
    #if row['amount'] > writable['auction'][row['auction']]['amount']:
      #  writable['auction'][row['auction']]['amount'] = row['amount']
    #if int(row['success']) == 1:
      #  writable['auction'][row['auction']]['success'] = 1
    # Update other features of the bidder
    writable['merchandise'].setdefault(row['merchandise'], 0)
    writable['merchandise'][row['merchandise']] += 1
    writable['device'].setdefault(row['device'], 0)
    writable['device'][row['device']] += 1
    writable['country'].setdefault(row['country'], 0)
    writable['country'][row['country']] += 1
    writable['ip'].setdefault(row['ip'], 0)
    writable['ip'][row['ip']] += 1
    writable['url'].setdefault(row['url'], 0)
    writable['url'][row['url']] += 1
    writable['time'].setdefault(row['time'], 0)
    writable['time'][row['time']] += 1

In [17]:
def argmax(d):
    """
    :param
    d: A dictionary
    :return:
    max_class: the key that have the maximum value of the dictionary
    max_value: the maximum value of the dictionary
    """
    max_value = 0
    max_class = None
    for key in d:
        if d[key] > max_value:
            max_value = d[key]
            max_class = key
    return max_value, max_class

In [18]:
def avg_auction(d, target):
    """
    :param
    d: An auction dictionary
    target: 'country', 'device', 'ip' or 'url'
    :return:
    avg_value: the average value of the target
    """
    sum_value = 0
    count = 0
    for key in d:
        current_value = len(d[key][target].keys())
        sum_value += current_value
        count += 1
    return float(sum_value) / count

In [19]:
def max_auction(d, target):
    """
    :param
    d: An auction dictionary
    target: 'country', 'device', 'ip' or 'url'
    :return:
    max_value: the maximum value of the target
    """
    max_value = 0
    for key in d:
        current_value = len(d[key][target].keys())
        if current_value > max_value:
            max_value = current_value
    return max_value

In [26]:
def min_auction(d, target):
    """
    :param
    d: An auction dictionary
    target: 'country', 'device', 'ip' or 'url'
    :return:
    min_value: the minimum value of the target
    """
    min_value = 9999
    for key in d:
        current_value = len(d[key][target].keys())
        if current_value < min_value:
            min_value = current_value
    return min_value

In [24]:
def avg_auction_time(d):
    """
    :param
    d: An auction dictionary
    :return:
    avg_time: the average time the bidder takes to make a bid
    """
    sum_times = 0
    count = 0
    for key in d:
        single_times = sum(d[key]['time'].values())
        sum_times += single_times
        count += 1
    return float(sum_times) / count

In [25]:
def avg_auction_time2(d):
    """
    :param
    d: An auction dictionary
    :return:
    avg_time: the average time the bidder takes to make a bid
    """
    sum_times = 0
    count = 0
    for key in d:
        single_times = np.array(d[key]['time'].values()).mean()
        sum_times += single_times
        count += 1
    return float(sum_times) / count

In [27]:
def auction_amount(d):
    """
    :param
    d: An auction dictionary
    :return:
    avg_amount: the average amount the bidder takes to make a bid
    max_amount: the maximum amount the bidder takes to make a bid
    min_amount: the minimum amount the bidder takes to make a bid
    """
    sum_amount = 0
    max_amount = 0
    min_amount = 99999999
    count = 0
    for key in d:
        amount = int(d[key]['amount'])
        sum_amount += amount
        count += 1
        if amount < min_amount:
            min_amount = amount
        if amount > max_amount:
            max_amount = amount
    return min_amount, float(sum_amount) / count, max_amount

In [28]:
def auction_success(d):
    """
    :param
    d: An auction dictionary
    :return:
    success_num: number of successful bid
    """
    num_success = 0
    for key in d:
        num_success += int(d[key]['success'])
    return num_success

In [34]:
for t, row in enumerate(DictReader(open(filename))):

    if t == 0:
        last_row = row
        update_writable(writable, row)
        continue

    if row['bidder_id'] != last_row['bidder_id']:
        if np.array(writable['time'].values()).mean() > 1:
            avg_times = 1
        else:
            avg_times = 0
        if np.array(writable['time'].values()).max() > 1:
            max_times = 1
        else:
            max_times = 0
        min_amount, avg_amount, max_amount = auction_amount(writable['auction'])
        write_row = [last_row['bidder_id'], writable['num'], avg_auction_time2(writable['auction']),
                     avg_auction_time(writable['auction']), avg_auction(writable['auction'], 'device'),
                     avg_auction(writable['auction'], 'country'), avg_auction(writable['auction'], 'ip'),
                     avg_auction(writable['auction'], 'url'), max_auction(writable['auction'], 'device'),
                     max_auction(writable['auction'], 'country'), max_auction(writable['auction'], 'ip'),
                     max_auction(writable['auction'], 'url'), min_auction(writable['auction'], 'device'),
                     min_auction(writable['auction'], 'country'), min_auction(writable['auction'], 'ip'),
                     min_auction(writable['auction'], 'url'), len(writable['auction'].keys()),
                     argmax(writable['merchandise'])[1], len(writable['merchandise'].keys()), argmax(writable['device'])[1],
                     len(writable['device'].keys()), argmax(writable['country'])[1],
                     len(writable['country'].keys()), argmax(writable['ip'])[1], len(writable['ip'].keys()),
                     argmax(writable['url'])[1], len(writable['url'].keys()), avg_times,
                     np.array(writable['time'].values()).min(), max_times, min_amount, avg_amount, max_amount,
                     auction_success(writable['auction'])]
        write_rows.append(write_row)
        count += 1
        writable = dict()
        write_row = list()

    update_writable(writable, row)

    if (count%1000 == 0) and (count != 0):
        print (t, count)

    last_row = row
open_file_object.writerows(write_rows)
open_file.close()

(1026, 1000)
(2049, 2000)
(3077, 3000)
(4105, 4000)
(5138, 5000)
(6178, 6000)
(7229, 7000)
(8272, 8000)
(9303, 9000)
(10344, 10000)
(11370, 11000)
(12398, 12000)
(13427, 13000)
(14470, 14000)
(15510, 15000)
(16562, 16000)
(17608, 17000)
(18646, 18000)
(19690, 19000)
(20725, 20000)
(21755, 21000)
(22788, 22000)
(23810, 23000)
(24844, 24000)
(25865, 25000)
(26898, 26000)
(27940, 27000)
(28964, 28000)
(29994, 29000)
(31036, 30000)
(32078, 31000)
(33113, 32000)
(34148, 33000)
(35180, 34000)
(36228, 35000)
(37265, 36000)
(38306, 37000)
(39344, 38000)
(40397, 39000)
(41443, 40000)
(42479, 41000)
(43526, 42000)
(44564, 43000)
(45609, 44000)
(46646, 45000)
(47680, 46000)
(48727, 47000)
(49758, 48000)
(50805, 49000)
(51843, 50000)
(52883, 51000)
(52884, 51000)
(53930, 52000)
(54977, 53000)
(55999, 54000)
(57020, 55000)
(58039, 56000)
(59062, 57000)
(60092, 58000)
(60093, 58000)
(61129, 59000)
(62168, 60000)
(63211, 61000)
(64239, 62000)
(65274, 63000)
(66308, 64000)
(67350, 65000)
(68384, 66000

In [4]:
import pandas as pd

In [35]:
arrange = pd.read_csv('arrange1.csv',nrows=10)

In [36]:
arrange.head()

bidder_id  bid_num  avg_auction_times  \
0  8dac2b259fd1c6d1120e519fb1ac14fbqvax8        3                  3   
1  668d393e858e8126275433046bbd35c6tywop        1                  1   
2  aa5f360084278b35d746fa6af3a7a1a5ra3xe        1                  1   
3  3939ac3ef7d472a59a9c5f893dd3e39fh9ofi        1                  1   
4  8393c48eaf4b8fa96886edc7cf27b372dsibi        1                  1   

   avg_auction  auc_device  auc_country  auc_ip  auc_url  auc_device_max  \
0            3           1            1       1        1               1   
1            1           1            1       1        1               1   
2            1           1            1       1        1               1   
3            1           1            1       1        1               1   
4            1           1            1       1        1               1   

   auc_country_max       ...         ip_num          max_url  url_num  \
0                1       ...              1  vasstdc27m7nks3        1   
1                1       ...              1  jmqlhflrzwuay9c        1   
2                1       ...              1  vasstdc27m7nks3        1   
3                1       ...              1  vasstdc27m7nks3        1   
4                1       ...              1  vasstdc27m7nks3        1   

   avg_times  min_times  max_times  min_amount avg_amount  max_amount  \
0          0          1          0           0          0           0   
1          0          1          0           0          0           0   
2          0          1          0           0          0           0   
3          0          1          0           0          0           0   
4          0          1          0           0          0           0   

  success_num  
0           0  
1           0  
2           0  
3           0  
4           0  

[5 rows x 34 columns]

In [39]:
import pandas as pd
import numpy as np
import csv

from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import (RandomForestClassifier, ExtraTreesClassifier,
                              AdaBoostClassifier, BaggingClassifier)
from sklearn.svm import SVC
from sklearn import cross_validation
from random import random, randint
from math import log, exp, sqrt,factorial
from sklearn import metrics
from sklearn.preprocessing import OneHotEncoder
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import StandardScaler

In [38]:
enc_device = OneHotEncoder()
lab_device = LabelEncoder()

In [37]:
import csv
from csv import DictReader

test_features = ['bidder_id', 'bid_num', 'auc_device', 'auc_country', 'auc_ip', 'auc_url',
            'auc_num', 'max_merch', 'merch_num', 'max_device', 'device_num', 'max_country',
            'country_num', 'max_ip', 'ip_num', 'max_url', 'url_num', 'address', 'account']
train_features = test_features[:]
train_features.append('outcome')

train = open('train.csv')
test = open('test.csv')
arrange = open('arrange1.csv')
train_bidder = dict()
test_bidder = dict()

In [40]:
pre_train = open("pre_train.csv", "wb")
pre_test = open("pre_test.csv", "wb")
open_file_train = csv.writer(pre_train)
open_file_test = csv.writer(pre_test)
open_file_train.writerow(train_features)
open_file_test.writerow(test_features)

In [41]:
import csv
from csv import DictReader

test_features = ['bidder_id', 'bid_num', 'auc_device', 'auc_country', 'auc_ip', 'auc_url',
            'auc_num', 'max_merch', 'merch_num', 'max_device', 'device_num', 'max_country',
            'country_num', 'max_ip', 'ip_num', 'max_url', 'url_num', 'address', 'account']
train_features = test_features[:]
train_features.append('outcome')

In [42]:
for row in DictReader(train):
    train_bidder.setdefault(row['bidder_id'], dict())
    train_bidder[row['bidder_id']]['account'] = row['payment_account']
    train_bidder[row['bidder_id']]['address'] = row['address']
    train_bidder[row['bidder_id']]['outcome'] = row['outcome']

In [43]:
for row in DictReader(test):
    test_bidder.setdefault(row['bidder_id'], dict())
    test_bidder[row['bidder_id']]['account'] = row['payment_account']
    test_bidder[row['bidder_id']]['address'] = row['address']

In [ ]:
for t, row in enumerate(arrange):
    if t == 0:
        continue
    row = row.strip().split(',')

    if row[0] in train_bidder:
        row.append(train_bidder[row[0]]['account'])
        row.append(train_bidder[row[0]]['address'])
        row.append(train_bidder[row[0]]['outcome'])
        del train_bidder[row[0]]
        open_file_train.writerow(row)

    elif row[0] in test_bidder:
        row.append(test_bidder[row[0]]['account'])
        row.append(test_bidder[row[0]]['address'])
        del test_bidder[row[0]]
        open_file_test.writerow(row)

    else:
        print row[0]

    if t % 1000 == 0:
        print t

8dac2b259fd1c6d1120e519fb1ac14fbqvax8
6c8ffec692e88d81e1b18d47818abb04v6llr
668d393e858e8126275433046bbd35c6tywop
aa5f360084278b35d746fa6af3a7a1a5ra3xe
a58ace8b671a7531c88814bc86b2a34cf0crb
a58ace8b671a7531c88814bc86b2a34cf0crb
ffbc0fdfbf19a8a9116b68714138f2902cc13
d174177146370aacbd5ae107b6be78828tx3e
668d393e858e8126275433046bbd35c6tywop
668d393e858e8126275433046bbd35c6tywop
6c8ffec692e88d81e1b18d47818abb04v6llr
ffbc0fdfbf19a8a9116b68714138f2902cc13
e8291466de91b0eb4e1515143c7f74dexy2yr
a58ace8b671a7531c88814bc86b2a34cf0crb
8393c48eaf4b8fa96886edc7cf27b372dsibi
e8291466de91b0eb4e1515143c7f74dexy2yr
fe37b8b29d26021ea9462bcc7c5bf5c2pbya7
c4856fd5abe8f6d6dea36ca2fec444faauos8
a58ace8b671a7531c88814bc86b2a34cf0crb
45972f59df79953d9bcf04a76dbe0f51z23qd
d174177146370aacbd5ae107b6be78828tx3e
6c8ffec692e88d81e1b18d47818abb04v6llr
668d393e858e8126275433046bbd35c6tywop
dd055846eb553ab8e953b084f2048d53bdqec
e8291466de91b0eb4e1515143c7f74dexy2yr
6c8ffec692e88d81e1b18d47818abb04v6llr
cd6e029b117d